In [ ]:
import pandas as pd
import numpy as np
import os
import requests
import datetime
import functools

# COLLECT RAW DATA

In [ ]:
os.makedirs('data_raw', exist_ok=True)
base_url = "https://www.football-data.co.uk/mmz4281/{}/E0.csv"
all_data = []

for year in range(2010, 2024):

    season = f'{str(year - 1)[-2:]}{str(year)[-2:]}'
    url = base_url.format(season)
    
    try:
        response = requests.get(url)
        response.raise_for_status()
        with open(f'data_raw/E0_{year}.csv', 'wb') as f:
            f.write(response.content)
        print(f'Successfully loaded data for season {year - 1}/{year}')

        season_data = pd.read_csv(f'data_raw/E0_{year}.csv')
        all_data.append(season_data)
    
    except requests.exceptions.RequestException as e:
        print(f'Error loading {url}: {e}')

if all_data:
    combined_data = pd.concat(all_data, ignore_index=True)    
    combined_data.to_csv(f'data_raw/E0_combined_2010_2023.csv', index=False)
    print(f'Successfully saved combined data')
else:
    print('No data was downloaded.')


Successfully loaded data for season 2009/2010
Successfully loaded data for season 2010/2011
Successfully loaded data for season 2011/2012
Successfully loaded data for season 2012/2013
Successfully loaded data for season 2013/2014
Successfully loaded data for season 2014/2015
Successfully loaded data for season 2015/2016
Successfully loaded data for season 2016/2017
Successfully loaded data for season 2017/2018
Successfully loaded data for season 2018/2019
Successfully loaded data for season 2019/2020
Successfully loaded data for season 2020/2021
Successfully loaded data for season 2021/2022
Successfully loaded data for season 2022/2023
Successfully saved combined data


# PREPROCESS DATA

In [53]:
def conjunction(*conditions):
    return functools.reduce(np.logical_and, conditions)

def union(*conditions):
    return functools.reduce(np.logical_or, conditions)

lookback_opp_matches = 3
lookback_matches = 5

In [ ]:
data = pd.read_csv(f'data_raw/E0_combined_2015_2023.csv')

# date format
data.dropna(subset=['Date'], inplace=True)
data = data.dropna(subset=['Date'])
data['Date'] = pd.to_datetime(data['Date'], errors='coerce')
print(data['Date'].isna().sum())
data = data.dropna(subset=['Date'])
data['Date'] = data['Date'].dt.strftime('%Y-%m-%d')

0


C:\Users\ADMIN\AppData\Local\Temp\ipykernel_6948\1982302444.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  data['Date'] = pd.to_datetime(data['Date'], errors='coerce')


In [ ]:
# average out betting odds
data['Hodds'] = np.mean(data[['B365H','BWH','IWH','LBH','PSH','WHH','SJH','VCH']],axis=1)
data['Dodds'] = np.mean(data[['B365D','BWD','IWD','LBD','PSD','WHD','SJD','VCD']],axis=1)
data['Aodds'] = np.mean(data[['B365A','BWA','IWA','LBA','PSA','WHA','SJA','VCA']],axis=1)

# Div,Date,HomeTeam,AwayTeam,FTHG,FTAG,FTR,HTHG,HTAG,HTR,Referee,HS,AS,HST,AST,HF,AF,HC
# ,AC,HY,AY,HR,AR,B365H,B365D,B365A,BWH,BWD,BWA,IWH,IWD,IWA,LBH,LBD,LBA,PSH,PSD,PSA,WHH,WHD,WHA,SJH
# ,SJD,SJA,VCH,VCD,VCA,Bb1X2,BbMxH,BbAvH,BbMxD,BbAvD,BbMxA,BbAvA,BbOU,BbMx>2.5,BbAv>2.5,BbMx<2.5,BbAv<2.5
# ,BbAH,BbAHh,BbMxAHH,BbAvAHH,BbMxAHA,BbAvAHA,PSCH,PSCD,PSCA

use_col = ['Date','HomeTeam','AwayTeam','FTHG','FTAG','FTR','HTHG','HTAG','HTR','Referee','HS','AS','HST','AST',
            'HC','AC','HF','AF','HY','AY','HR','AR','Hodds','Dodds','Aodds']
data = data[use_col]


In [56]:
acc_hist = {'home_wins' : [], 'home_draws' : [], 'home_losses' : [], 'home_goals' : [], 'home_oppos_goals' : [],
            'home_shots' : [], 'home_oppos_shots' : [], 'home_shotontarget' : [], 'home_oppos_shotontarget' : [],
            'away_wins' : [], 'away_draws' : [], 'away_losses' : [], 'away_goals' : [], 'away_oppos_goals' : [],
            'away_shots' : [], 'away_oppos_shots' : [], 'away_shotontarget' : [], 'away_oppos_shotontarget' : [],
            'home_oppos_wins' : [], 'home_oppos_draws' : [], 'home_oppos_losses' : [],
            'home_fouls' : [], 'home_yellowcards' : [], 'home_redcards' : [], 'home_cornerkicks' : [],
            'home_oppos_cornerkicks' : [], 'home_oppos_fouls' : [], 'home_oppos_yellowcards' : [], 'home_oppos_redcards' : [],
            'away_fouls' : [], 'away_yellowcards' : [], 'away_redcards' : [], 'away_cornerkicks' : [],
            'away_oppos_cornerkicks' : [],'away_oppos_fouls' : [], 'away_oppos_yellowcards' : [], 'away_oppos_redcards' : []}
d = 0


In [57]:
for row in data.iterrows() :
    hometeam = row[1]['HomeTeam']
    awayteam = row[1]['AwayTeam']
    date = row[1]['Date']

    # filter matches with same playing teams
    temp1 = data[conjunction(data['HomeTeam']==hometeam, data['AwayTeam']==awayteam)]
    temp2 = data[conjunction(data['HomeTeam']==awayteam, data['AwayTeam']==hometeam)]
    temp = pd.concat([temp1, temp2], axis=0)
    history = temp[temp['Date']<date].sort_values(by='Date').tail(lookback_opp_matches)
    # if opponent history is too short, continue
    if len(history) < lookback_opp_matches :
        for key in list(acc_hist.keys()) :
            acc_hist[key].append(np.nan)
        continue

    # compute average number of goals scored against opponent in the past N matches with the opponent
    home = history[history['HomeTeam'] == hometeam]
    away = history[history['AwayTeam'] == hometeam]
    home_sum = np.sum(home[['FTHG','FTAG','HS','AS','HST','AST','HC','AC','HF','AF','HY','AY','HR','AR']])
    away_sum = np.sum(away[['FTHG','FTAG','HS','AS','HST','AST','HC','AC','HF','AF','HY','AY','HR','AR']])


    # filter recent N matches of both home and away
    home = data[union(data['HomeTeam']==hometeam, data['AwayTeam']==hometeam)]
    home = home[home['Date']<date].sort_values(by='Date').tail(lookback_matches)
    away = data[union(data['HomeTeam']==awayteam, data['AwayTeam']==awayteam)]
    away = away[away['Date']<date].sort_values(by='Date').tail(lookback_matches)

    # if match history is too short, continue
    if len(home) < lookback_matches or len(away) < lookback_matches :
        for key in list(acc_hist.keys()) :
            acc_hist[key].append(np.nan)
        continue

    home_home_sum = np.sum(home[home['HomeTeam']==hometeam][['FTHG','HS','HST','HC','HF','HY','HR']])
    home_away_sum = np.sum(home[home['AwayTeam']==hometeam][['FTAG','AS','AST','AC','AF','AY','AR']])
    away_home_sum = np.sum(away[away['HomeTeam']==awayteam][['FTHG','HS','HST','HC','HF','HY','HR']])
    away_away_sum = np.sum(away[away['AwayTeam']==awayteam][['FTAG','AS','AST','AC','AF','AY','AR']])

    # append computation results to dictionary
    acc_hist['home_oppos_goals'].append((home_sum['FTHG'] + away_sum['FTAG']) / lookback_opp_matches)
    acc_hist['away_oppos_goals'].append((home_sum['FTAG'] + away_sum['FTHG']) / lookback_opp_matches)
    acc_hist['home_oppos_shots'].append((home_sum['HS'] + away_sum['AS']) / lookback_opp_matches)
    acc_hist['away_oppos_shots'].append((home_sum['AS'] + away_sum['HS']) / lookback_opp_matches)
    acc_hist['home_oppos_shotontarget'].append((home_sum['HST'] + away_sum['AST']) / lookback_opp_matches)
    acc_hist['away_oppos_shotontarget'].append((home_sum['AST'] + away_sum['HST']) / lookback_opp_matches)
    acc_hist['home_oppos_cornerkicks'].append((home_sum['HC'] + away_sum['AC']) / lookback_opp_matches)
    acc_hist['away_oppos_cornerkicks'].append((home_sum['AC'] + away_sum['HC']) / lookback_opp_matches)
    acc_hist['home_oppos_fouls'].append((home_sum['HF'] + away_sum['AF']) / lookback_opp_matches)
    acc_hist['away_oppos_fouls'].append((home_sum['AF'] + away_sum['HF']) / lookback_opp_matches)
    acc_hist['home_oppos_yellowcards'].append((home_sum['HY'] + away_sum['AY']) / lookback_opp_matches)
    acc_hist['away_oppos_yellowcards'].append((home_sum['AY'] + away_sum['HY']) / lookback_opp_matches)
    acc_hist['home_oppos_redcards'].append((home_sum['HR'] + away_sum['AR']) / lookback_opp_matches)
    acc_hist['away_oppos_redcards'].append((home_sum['AR'] + away_sum['HR']) / lookback_opp_matches)

    acc_hist['home_goals'].append((home_home_sum['FTHG'] + home_away_sum['FTAG']) / lookback_matches)
    acc_hist['away_goals'].append((away_home_sum['FTHG'] + away_away_sum['FTAG']) / lookback_matches)
    acc_hist['home_shots'].append((home_home_sum['HS'] + home_away_sum['AS']) / lookback_matches)
    acc_hist['away_shots'].append((away_home_sum['HS'] + away_away_sum['AS']) / lookback_matches)
    acc_hist['home_shotontarget'].append((home_home_sum['HST'] + home_away_sum['AST']) / lookback_matches)
    acc_hist['away_shotontarget'].append((away_home_sum['HST'] + away_away_sum['AST']) / lookback_matches)
    acc_hist['home_cornerkicks'].append((home_home_sum['HC'] + home_away_sum['AC']) / lookback_matches)
    acc_hist['away_cornerkicks'].append((away_home_sum['HC'] + away_away_sum['AC']) / lookback_matches)
    acc_hist['home_fouls'].append((home_home_sum['HF'] + home_away_sum['AF']) / lookback_matches)
    acc_hist['away_fouls'].append((away_home_sum['HF'] + away_away_sum['AF']) / lookback_matches)
    acc_hist['home_yellowcards'].append((home_home_sum['HY'] + home_away_sum['AY']) / lookback_matches)
    acc_hist['away_yellowcards'].append((away_home_sum['HY'] + away_away_sum['AY']) / lookback_matches)
    acc_hist['home_redcards'].append((home_home_sum['HR'] + home_away_sum['AR']) / lookback_matches)
    acc_hist['away_redcards'].append((away_home_sum['HR'] + away_away_sum['AR']) / lookback_matches)


    # count ratio of wins / draws / losses in the past N matches of Home vs Away
    res = []
    for r in history.iterrows() :
        if r[1]['HomeTeam'] == hometeam :
            res.append(r[1]['FTR'])
        else :
            if r[1]['FTR'] == 'A' :
                res.append('H')
            elif r[1]['FTR'] == 'H' :
                res.append('A')
            else :
                res.append('D')
    acc_hist['home_oppos_wins'].append(res.count('H') / lookback_opp_matches)
    acc_hist['home_oppos_draws'].append(res.count('D') / lookback_opp_matches)
    acc_hist['home_oppos_losses'].append(res.count('A') / lookback_opp_matches)


    # count ratio of wins / draws / losses in the past N matches
    res = []
    for r in home.iterrows() :
        if r[1]['HomeTeam'] == hometeam :
            res.append(r[1]['FTR'])
        else :
            if r[1]['FTR'] == 'A' :
                res.append('H')
            elif r[1]['FTR'] == 'H' :
                res.append('A')
            else :
                res.append('D')
    acc_hist['home_wins'].append(res.count('H') / lookback_matches)
    acc_hist['home_draws'].append(res.count('D') / lookback_matches)
    acc_hist['home_losses'].append(res.count('A') / lookback_matches)

    res = []
    for r in away.iterrows() :
        if r[1]['HomeTeam'] == awayteam :
            res.append(r[1]['FTR'])
        else :
            if r[1]['FTR'] == 'A' :
                res.append('H')
            elif r[1]['FTR'] == 'H' :
                res.append('A')
            else :
                res.append('D')
    acc_hist['away_wins'].append(res.count('H') / lookback_matches)
    acc_hist['away_draws'].append(res.count('D') / lookback_matches)
    acc_hist['away_losses'].append(res.count('A') / lookback_matches)

acc_hist = pd.DataFrame(acc_hist)

f:\Apps\miniconda3\Lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning: The behavior of DataFrame.sum with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return reduction(axis=axis, out=out, **passkwargs)
f:\Apps\miniconda3\Lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning: The behavior of DataFrame.sum with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return reduction(axis=axis, out=out, **passkwargs)
f:\Apps\miniconda3\Lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning: The behavior of DataFrame.sum with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return reduction(axis=axis, out=out, **passkwargs)
f:\Apps\mi

In [ ]:
data = pd.concat([data, acc_hist], axis=1)
data.drop(columns=['FTHG','FTAG','HTHG','HTAG','HTR','Referee','HS','AS','HST','AST',
            'HC','AC','HF','AF','HY','AY','HR','AR'], inplace=True)
data.rename(columns={'FTR' : 'Result'}, inplace=True)
data.dropna(inplace=True)
data.to_csv('data_processed/E0.csv', index=False)

# SPLIT PROCESSED DATA

In [75]:
test_years = [2022, 2023]
val_years = [2021]

In [76]:
test = data[pd.to_datetime(data['Date']).dt.year.apply(lambda x : x in test_years)]
val = data[pd.to_datetime(data['Date']).dt.year.apply(lambda x : x in val_years)]
train = data[pd.to_datetime(data['Date']).dt.year.apply(lambda x : x not in [test_years, val_years])]

test.to_csv('data_processed/test.csv', index=False)
val.to_csv('data_processed/val.csv', index=False)
train.to_csv('data_processed/train.csv', index=False)